### BUFR and GRIB data import and visualization
Notebook prepared by Ben Maathuis, Bas Retsios and Willem Nieuwenhuis. ITC-University of Twente, Enschede. The Netherlands

Within this notebook we are going to process data which has been made available through EUMETCast (https://en.wikipedia.org/wiki/Eumetcast). Some of the data provided is in a format commonly used by the meteorological survices, like BUFR (a binary data format standardized by the World Meteorological Organization (WMO) -  https://en.wikipedia.org/wiki/BUFR) and GRIB (GRIdded Binary is a data format developed by the World Meteorological Organization (WMO) for storing and exchanging gridded meteorological data - https://en.wikipedia.org/wiki/GRIB).

First we are going to process some atmospheric motion vectorss (AMV), for details on this product see the product navigator at EUMETSAT (https://navigator.eumetsat.int/product/EO:EUM:CM:MSG:MSGAMVE0100?query=amv&results=20&s=advanced)

We are going to use a python library called pybufrkit - see: https://pybufrkit.readthedocs.io/en/latest/ 

To plot AMV's see also: https://dwikita-ichsana.medium.com/meteorology-101-how-to-plot-wind-map-e43c196edce8

The sample data is available in the zip file "BUFR_GRIB_data" and is expected in the root of the notebook folder

In [ ]:
#if pybufrkit is not installed, uncomment the line below
#!pip install pybufrkit

In [ ]:
# Note from the module import section in the colde field below the line: from mpl_toolkits.basemap import Basemap
# If you get a message: 'No module named 'mpl_toolkits.basemap', uncomment the line below
#!pip install basemap

In [ ]:
#import the modules - libraries
import os
import ilwis
import shutil
import glob 
import numpy as np
import pandas as pd
import matplotlib.pyplot as plt
from matplotlib import cm
import matplotlib.colors as mcolors
from sklearn import preprocessing
from pybufrkit.decoder import Decoder
from pybufrkit.mdquery import MetadataExprParser, MetadataQuerent
from pybufrkit.dataquery import NodePathParser, DataQuerent
import subprocess
from glob import glob
#from osgeo import osr, ogr
import geopandas as gpd
from shapely.geometry import Point
from mpl_toolkits.basemap import Basemap

import warnings
warnings.filterwarnings('ignore')

In [ ]:
work_dir = os.getcwd() + '/BUFR_GRIB_data'
 #set the working directory for ILWISPy
ilwis.setWorkingCatalog(work_dir)
print(work_dir)

#### Load bufr file and review the meta data - content descriptions

In [ ]:
# Decode a AMV BUFR file
# BUFR input file
file_in = work_dir+r'/W_XX-EUMETSAT-Darmstadt,SING+LEV+SAT,MET10+AMV_C_EUMG_20250714133000_3.bin'
print(file_in)

In [ ]:
#split all messages contained in BUFR file into seperate messages
#check the data folder and note all 'seperate' message files created with extenstion *.bin.0 to *.bin.n
subprocess.run(['pybufrkit', 'split', file_in])

In [ ]:
#read all messages and append 
messages = []
decoder = Decoder()
path = file_in
filelist = glob(path + '.*')
for file in filelist:
    with open((file), 'rb') as ins:
        bufr_message = decoder.process(ins.read())
        messages.append(bufr_message)

In [ ]:
# Query the metadata
n_subsets = MetadataQuerent(MetadataExprParser()).query(bufr_message, '%n_subsets')
print(n_subsets)

In [ ]:
# Decode only the metadata sections of a BUFR file
result = subprocess.run(['pybufrkit', 'info', file_in], capture_output=True)
result = result.stdout.decode('utf-8')
print(result)

#### Retrieve parameters from BUFR file

In [ ]:
# Review the content listing of the unexpanded_descriptors - should be 6 digits!
BUFR_parameter = '310077'

In [ ]:
result1 = subprocess.run(['pybufrkit', 'lookup', '-l', BUFR_parameter], capture_output=True)
result1 = result1.stdout.decode('utf-8')
print(result1)

In [ ]:
# select a relevant parameter
BUFR_parameter = '007004' #note 6 digits
result2 = subprocess.run(['pybufrkit', 'lookup', '-l', BUFR_parameter], capture_output=True)
result2 = result2.stdout.decode('utf-8')
print(result2)

In [ ]:
#extract a parameter for a given message, note the OrderedDict extracted
LAT_result = DataQuerent(NodePathParser()).query(bufr_message, '005001') # see LATITUDE (HIGH ACCURACY)
print(LAT_result.results)

In [ ]:
#retrieve the first item from each tuple in the OrderedDict
lats=[LAT_result.results[key][0] for key in LAT_result.results.keys()]
print(lats)

In [ ]:
# Get the number of records for this message
num_records = len(lats)
print(num_records)

In [ ]:
#longitude
LON_result = DataQuerent(NodePathParser()).query(bufr_message, '006001')
#uncomment the line below to see the results
#print(LON_result.results)

In [ ]:
lons=[LON_result.results[key][0] for key in LON_result.results.keys()]
#print(lons)

In [ ]:
#Wind_U
WINDU_result = DataQuerent(NodePathParser()).query(bufr_message, '011003')
#uncomment the line below to see the results
#print(WINDU_result.results)

In [ ]:
windus=[WINDU_result.results[key][0] for key in WINDU_result.results.keys()]
#uncomment the line below to see the results
#print(windus)

In [ ]:
#Wind_V
WINDV_result = DataQuerent(NodePathParser()).query(bufr_message, '011004')
#uncomment the line below to see the results
#print(WINDV.results)

In [ ]:
windvs=[WINDV_result.results[key][0] for key in WINDV_result.results.keys()]

In [ ]:
#pressure
PRESSURE_result = DataQuerent(NodePathParser()).query(bufr_message, '007004')
#print(PRESSURE_result.results)

In [ ]:
press=[PRESSURE_result.results[key][0] for key in PRESSURE_result.results.keys()]
#print(press)

#### Now conduct the import of all required parameters (lat, lon, windsv, windsu and press) in a singe loop

In [ ]:
#retrieve various BUFR parameters, for all messages in a single loop
lats = np.array([])
lons = np.array([])
windvs = np.array([])
windus = np.array([])
press = np.array([])

for  message in messages:
    LAT_result = DataQuerent(NodePathParser()).query(message, '005001')
    lats=np.concatenate((lats, np.array([LAT_result.results[key][0] for key in LAT_result.results.keys()])))
    LON_result = DataQuerent(NodePathParser()).query(message, '006001')
    lons=np.concatenate((lons,np.array([LON_result.results[key][0] for key in LON_result.results.keys()])))
    WINDV_result = DataQuerent(NodePathParser()).query(message, str('011004'))
    windvs=np.concatenate((windvs,np.array([WINDV_result.results[key][0] for key in WINDV_result.results.keys()])))
    WINDU_result = DataQuerent(NodePathParser()).query(message, str('011003'))
    windus=np.concatenate((windus,np.array([WINDU_result.results[key][0] for key in WINDU_result.results.keys()])))
    PRESSURE_result = DataQuerent(NodePathParser()).query(message, str('007004'))
    press=np.concatenate((press,np.array([PRESSURE_result.results[key][0] for key in PRESSURE_result.results.keys()])))

In [ ]:
# Get the number of records for all messages
num_records = len(lats)
print(num_records)

In [ ]:
#to compare with results of individual parameter extraction uncomment the line below
#print(press)

In [ ]:
# Scatter plot of pressure data
vals = press  # your pressure values

# Create normalized color values
norm = mcolors.Normalize(vmin=min(vals), vmax=max(vals))
colormap = cm.rainbow

plt.figure(figsize=(6,6))

# Plot scatter with colormap
sc = plt.scatter(lons, lats, c=vals, cmap=colormap, norm=norm, marker='.')

# Add colorbar as legend
cbar = plt.colorbar(sc, fraction=0.0235, pad=0.03, shrink=0.5)
cbar.set_label('Pressure - Pa')  # Label for the colorbar

plt.xlabel('Longitude')
plt.ylabel('Latitude')
plt.title('Pressure')
plt.xlim(-67.5, 67.5)
plt.ylim(-67.5, 67.5)

plt.show()


In [ ]:
# convert numpy array to pandas dataframe and add 3 more columns (WINDSP, X and Y)
dataset = pd.DataFrame({'LAT': lats, 'LON': lons, 'WINDV': windvs, 'WINDU': windus, 'WINDSP':np.nan, 'PRESSURE':press, 'X':np.nan, 'Y':np.nan})
dataset

If wind speed is given as eastward and northward components (u and v), the overall wind speed (ws) can be calculated using the Pythagorean theorem: ws = √(u² + v²). 

In [ ]:
#Calculate the Windspeed
dataset['WINDSP'] = np.sqrt(dataset['WINDV']**2+dataset['WINDV']**2)
dataset

In [ ]:
#save the preliminary results as a csv file
dataset.to_csv(work_dir+'/AMV_bufr_out.csv')

In [ ]:
#check your folder and note the additional messages created
#remove obsolete files, here the seperate messages extracted
for p in glob(work_dir+'/*.bin.*', recursive=True):
    if os.path.isfile(p):
        os.remove(p)

### Changing projection - visualization

In [ ]:
#retreive the latitude and longitude coordinates (per pixel - row) and transform these into Meteosat Geostationary 'GEOS' projection X and Y

csyLL = ilwis.CoordinateSystem('epsg:4326') #define latlon to be used as input
csyGeos = ilwis.CoordinateSystem('code=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563')#define GEOS - geostationary projection to be used as output

#conduct the transformation
for index, row in dataset.iterrows():
    crdGeos = csyGeos.coord2coord(csyLL, ilwis.Coordinate(row['LON'],row['LAT']))
    dataset.loc[index, 'X'] = crdGeos.x
    dataset.loc[index, 'Y'] = crdGeos.y

dataset

In [ ]:
#get minimum and maximum value of a parameter
PARAM_Min = (dataset['PRESSURE'].min())
PARAM_Max = (dataset['PRESSURE'].max())
print(PARAM_Min)
print(PARAM_Max)

In [ ]:
#resample the point data set to a raster given an aggregation factor
# Set aggregation Factor - See https://user.eumetsat.int/s3/eup-strapi-media/pdf_msg_met_prod_atbd_15e4917e25.pdf page 28
aggregate_factor = 32 # Can be 1, 3, 16 or 32

In [ ]:
#mapping of selected parameter
x_size = int(3712 / aggregate_factor)
y_size = int(3712 / aggregate_factor)

xmin = -5568748.28
ymin = -5568748.28
xmax = 5568748.28
ymax = 5568748.28

pixel_size_x = (xmax - xmin) / x_size
pixel_size_y = (ymax - ymin) / y_size
print(x_size, y_size, pixel_size_x, pixel_size_y)
data = np.full((y_size, x_size), -9999, dtype=np.float64)
count = np.full((y_size, x_size), 0, dtype=np.float64)

#retrieve the mean data value of all initial values within the new raster resolution cell. If more coordinate pairs fall within the same pixel
#the average value is computed (using the count). This is only done for those pixels not having the value of -9999 
for index, row in dataset.iterrows():
    xpos = int((row['X'] - xmin) / pixel_size_x)
    ypos = y_size - int((row['Y'] - ymin) / pixel_size_y) - 1
    data[ypos,xpos] = row['PRESSURE'] if data[ypos,xpos] == -9999 else data[ypos,xpos] + row['PRESSURE']
    count[ypos,xpos] += 1
data[count>0] /= count[count>0] # calculate the average for the new pixel using the number of counts

In [ ]:
#new shape - raster dimensions
print(np.shape(data))

In [ ]:
#create a new ilwis raster
grf = ilwis.GeoReference('code=georef:type=corners,csy=proj4:+proj=geos +h=35785831 +a=6378137 +rf=298.257223563,envelope='+ str(xmin) + ' ' + str(ymax) + ' ' + str(xmax) + ' ' + str(ymin) + ',gridsize=' + str(x_size) + ' ' + str(y_size) + ',cornerofcorners=yes')
dfNum = ilwis.DataDefinition(ilwis.NumericDomain('code=value'), ilwis.NumericRange(PARAM_Min, PARAM_Max, 0))
rcNew = ilwis.RasterCoverage()
rcNew.setSize(ilwis.Size(x_size,y_size,1))
rcNew.setGeoReference(grf)
rcNew.setDataDef(dfNum)

In [ ]:
#fill the new raster with the data calulated above
rcNew.array2raster(data.flatten())
print(rcNew.size())

In [ ]:
#for all pixels with no data set the value to -9999
rcNew1 = ilwis.do('mapcalc', 'iff(@1==?,-9999, @1)',rcNew) 

In [ ]:
#create a new numpy array
p_2np = np.fromiter(iter(rcNew1), np.float64, rcNew1.size().linearSize()) 
p_2np = p_2np.reshape((rcNew1.size().ysize, rcNew1.size().xsize))

In [ ]:
#mask the array using the value of -9999
p_maskarray = np.ma.masked_where(p_2np == -9999, p_2np)
#p_maskarray.shape

In [ ]:
#plot the dataset using imshow - note the coordinates (metric - geostationary - origin is in the display centre!)
cf = plt.imshow(p_maskarray/100, extent=[xmin, xmax, ymin, ymax], origin='upper', vmin=PARAM_Min/100, vmax=PARAM_Max/100, interpolation = 'None', cmap='jet')
cb = plt.colorbar(cf, fraction=0.0235, pad=0.03, shrink=0.6 )
cb.set_label('hPa',  fontsize=15)
plt.xlabel('X Coordinate (meters)')
plt.ylabel('Y Coordinate (meters)')
plt.title('Aggregated (average) Pressure Map')
plt.show()

In [ ]:
#store resulting map - check in ilwis386
rcNew1.store('pressure.mpr')

In [ ]:
#transform raster created above to new Geographic lat-lon coordinates
#create target georeference
#note new window selected envelope=-10 -15 50 -35 (southern hemisphere), with a different gridsize=600 200, 

column_size = 600
row_size = 200

lat_min = -35
lat_max = -10
lon_min = -10
lon_max = 60

grfTarget = ilwis.GeoReference('code=georef:type=corners, csy=epsg:4326, envelope='+ str(lon_min) + ' ' + str(lat_max) + ' ' + str(lon_max) + ' ' + str(lat_min) + ',gridsize=' + str(row_size) + ' ' + str(column_size) + ',cornerofcorners=yes')

In [ ]:
#conduct the resampling operation
rc_res = ilwis.do('resample', rcNew1, grfTarget,'nearestneighbour')#'bilinear')

In [ ]:
#transform to numpy array
p_2np = np.fromiter(iter(rc_res), np.float64, rc_res.size().linearSize()) 
p_2np = p_2np.reshape((rc_res.size().ysize, rc_res.size().xsize))

In [ ]:
#review the shape of the new 2D array
p_2np.shape

In [ ]:
#mask the no-data
p_maskedarray = np.ma.masked_where(p_2np == -9999, p_2np)

In [ ]:
#plot the figure - 2 D array - note pressure is now in hPa
plt.figure(figsize=(8,6))

cf = plt.imshow(p_maskedarray/100, extent=[lon_min, lon_max, lat_min, lat_max], origin='upper', vmin=PARAM_Min/100, vmax=PARAM_Max/100, interpolation = 'None', cmap='jet')
cb = plt.colorbar(cf, fraction=0.0235, pad=0.03, shrink=0.4 )
cb.set_label('hPa',  fontsize=15)
plt.title('Pressure')
plt.xlabel('Longitude')
plt.ylabel('Latitude')

plt.show()

In [ ]:
#store resulting map
rc_res.store('pressure_LL.mpr')

In [ ]:
#create a new visualization using the wind direction (as arrows) and windspeed (as background map)
#Use quiver -see: https://matplotlib.org/stable/gallery/images_contours_and_fields/quiver_simple_demo.html 
#Use Matplotlib Basemap - see: https://matplotlib.org/basemap/stable/
plt.figure(figsize=(12,10))
img_extent = (-10, 50, -35, -15)

colvals = preprocessing.minmax_scale(vals)
#plt.scatter(lons, lats, color=cm.rainbow(colvals), marker='.')
Q = plt.quiver(lons[::10],lats[::10],windus[::10],windvs[::10], scale_units='xy', scale=6, width=0.0015,color ='black')

cf = plt.imshow(p_maskedarray/100, extent=img_extent, vmin=PARAM_Min/100, vmax=PARAM_Max/100, interpolation = 'None', cmap='turbo')

cb = plt.colorbar(cf, fraction=0.0235, pad=0.03, shrink=0.35 )
cb.set_label('hPa',  fontsize=10)

m = Basemap(projection='cyl', llcrnrlon=-10, llcrnrlat=-35, urcrnrlon=50, urcrnrlat=-15, resolution='i')
m.drawcoastlines(1)
m.drawcountries()

parallels = np.arange(-35,-15+0.25,10)
m.drawparallels(parallels, labels=[1,0,0,0], linewidth=0.5);
meridians = np.arange(-10,50+0.25,10)
m.drawmeridians(meridians, labels=[0,0,0,1], linewidth=0.5);

plt.show()

In [ ]:
#create a new visualization using the wind direction (as barbs) and windspeed (as background map)
#see also: https://pilotinstitute.com/surface-analysis-charts-explained/#wind
#matplotlib barbs example - see: https://matplotlib.org/stable/gallery/images_contours_and_fields/barb_demo.html
#Use Matplotlib Basemap - see: https://matplotlib.org/basemap/stable/
plt.figure(figsize=(16,10))

# Default parameters
#plt.barbs(lons[::1],lats[::1],windus[::1],windvs[::1])

#plot every 3rd element
#don't round the values
#don't show empty barbs

plt.barbs(lons[::3],lats[::3],windus[::3],windvs[::3],np.sqrt(windus[::3] ** 2 + windvs[::3] ** 2), fill_empty=False, rounding=False,
    sizes=dict(emptybarb=0.0, spacing=0.2, height=0.5), pivot='middle', cmap='turbo', zorder=3)

m = Basemap(projection='cyl', llcrnrlon=-10, llcrnrlat=-35, urcrnrlon=50, urcrnrlat=-15, resolution='i')
m.drawcoastlines(0.5)
m.drawcountries()

#note different background options
#m.drawmapboundary(fill_color='aqua')
#m.fillcontinents(color='yellow', lake_color='aqua')
#m.shadedrelief()
m.etopo(alpha =0.5) #set transparency


parallels = np.arange(-35,-15+0.25,10)
m.drawparallels(parallels, labels=[1,0,0,0], linewidth=0.5);
meridians = np.arange(-10,50+0.25,10)
m.drawmeridians(meridians, labels=[0,0,0,1], linewidth=0.5);

plt.show()

### Retrieve all atmospheric motion vectors at pressure levels below a certain threshold

In [ ]:
#enter threshold pressure value in Pascal
threshold = 70000 #700 hPa

In [ ]:
dataset['HP'] = dataset['PRESSURE'].apply(lambda x: x if x <= threshold else np.nan)
dataset['HP'] = dataset['PRESSURE']/100
#Pressure unit is Pascal
dataset['HWV'] = dataset['WINDV'].where(dataset['PRESSURE'] <= threshold, np.nan)
dataset['HWU'] = dataset['WINDU'].where(dataset['PRESSURE'] <= threshold, np.nan)

In [ ]:
#check the selected records
dataset

In [ ]:
hwv = dataset['HWV']
hwu = dataset['HWU']

In [ ]:
#matplotlib barbs example - see: https://matplotlib.org/stable/gallery/images_contours_and_fields/barb_demo.html
#Use Matplotlib Basemap - see: https://matplotlib.org/basemap/stable/
plt.figure(figsize=(16,10))

# Default parameters
#plt.barbs(lons[::1],lats[::1],windus[::1],windvs[::1])

#plot every element selected
#don't round the values
#don't show empty barbs

plt.barbs(lons[::1],lats[::1],hwu[::1],hwv[::1],np.sqrt(hwu[::1] ** 2 + hwv[::1] ** 2), fill_empty=False, rounding=False,
    sizes=dict(emptybarb=0.0, spacing=0.2, height=0.5), pivot='middle', cmap='turbo', zorder=3)

m = Basemap(projection='cyl', llcrnrlon=-10, llcrnrlat=-35, urcrnrlon=50, urcrnrlat=-15, resolution='i')
m.drawcoastlines(0.5)
m.drawcountries()

#note different background options
#m.drawmapboundary(fill_color='aqua')
#m.fillcontinents(color='yellow', lake_color='aqua')
#m.shadedrelief()
m.etopo(alpha =0.5) #set transparency


parallels = np.arange(-35,-15+0.25,10)
m.drawparallels(parallels, labels=[1,0,0,0], linewidth=0.5);
meridians = np.arange(-10,50+0.25,10)
m.drawmeridians(meridians, labels=[0,0,0,1], linewidth=0.5);

plt.show()

In [ ]:
#Example code to experiment with the wind visualization parameters
#reference: https://matplotlib.org/stable/gallery/images_contours_and_fields/barb_demo.html

x = np.linspace(-5, 5, 5)
X, Y = np.meshgrid(x, x)
U, V = 12 * X, 12 * Y

data = [(-1.5, .5, -6, -6),
        (1, -1, -46, 46),
        (-3, -1, 11, -11),
        (1, 1.5, 80, 80),
        (0.5, 0.25, 25, 15),
        (-1.5, -0.5, -5, 40)]

data = np.array(data, dtype=[('x', np.float32), ('y', np.float32),
                             ('u', np.float32), ('v', np.float32)])

fig1, axs1 = plt.subplots(nrows=2, ncols=2)
# Default parameters, uniform grid
axs1[0, 0].barbs(X, Y, U, V)

# Arbitrary set of vectors, make them longer and change the pivot point
# (point around which they're rotated) to be the middle
axs1[0, 1].barbs(
    data['x'], data['y'], data['u'], data['v'], length=8, pivot='middle')

# Showing colormapping with uniform grid.  Fill the circle for an empty barb,
# don't round the values, and change some of the size parameters
axs1[1, 0].barbs(
    X, Y, U, V, np.sqrt(U ** 2 + V ** 2), fill_empty=True, rounding=False,
    sizes=dict(emptybarb=0.25, spacing=0.2, height=0.3))

# Change colors as well as the increments for parts of the barbs
axs1[1, 1].barbs(data['x'], data['y'], data['u'], data['v'], flagcolor='r',
                 barbcolor=['b', 'g'], flip_barb=True,
                 barb_increments=dict(half=10, full=20, flag=100))

# Masked arrays are also supported
masked_u = np.ma.masked_array(data['u'])
masked_u[4] = 1000  # Bad value that should not be plotted when masked
masked_u[4] = np.ma.masked

#### Processing global instabillity index bufr data: the K-Index
See for additional product information: https://navigator.eumetsat.int/product/EO:EUM:DAT:0328?query=GII%20msg%200%20&s=advanced

In [ ]:
# Decode a AMV BUFR file
# BUFR input file
file_in = work_dir+r'/W_XX-EUMETSAT-Darmstadt,SING+LEV+SAT,MET10+GII_C_EUMG_20240612111500_3.bin'

In [ ]:
#split all messages contained in BUFR file into seperate messages
subprocess.run(['pybufrkit', 'split', file_in])

In [ ]:
#read all messages and append 
messages = []
decoder = Decoder()
path = file_in
filelist = glob(path + '.*')
for file in filelist:
    with open((file), 'rb') as ins:
        bufr_message = decoder.process(ins.read())
        messages.append(bufr_message)

In [ ]:
# Query the metadata
n_subsets = MetadataQuerent(MetadataExprParser()).query(bufr_message, '%n_subsets')
print(n_subsets)

In [ ]:
# Decode only the metadata sections of a BUFR file
result1 = subprocess.run(['pybufrkit', 'info', file_in], capture_output=True)
result1 = result1.stdout.decode('utf-8')
print(result1)

In [ ]:
#get further information about all non expanded_descriptors, first create a listing
nv = {}
for el in result1.split('\r\n'):
    data = el.split('=')
    if len(data)==2:
        key = data[0]
        val = data[1]
        nv[key.strip()]=val.strip()

In [ ]:
#check the resulting listing
print(nv)
print()
print(nv['unexpanded_descriptors'])

In [ ]:
#remove the [] and , and then loop through the descriptors listing
for BUFR_parameter in nv['unexpanded_descriptors'].lstrip('[').rstrip(']').split(','):
    BUFR_parameter = BUFR_parameter.strip()
    result1 = subprocess.run(['pybufrkit', 'lookup', '-l', BUFR_parameter], capture_output=True)
    result1 = result1.stdout.decode('utf-8')
    print(result1)

In [ ]:
# see: unexpanded_descriptors = '013044'
BUFR_parameter = '013044'

In [ ]:
result_BUFR = subprocess.run(['pybufrkit', 'lookup', '-l', BUFR_parameter], capture_output=True)
result_BUFR = result_BUFR.stdout.decode('utf-8')
print(result_BUFR)

In [ ]:
param = DataQuerent(NodePathParser()).query(bufr_message, BUFR_parameter)
print(param.results)

In [ ]:
vals=[param.results[key][0] for key in param.results.keys()]
#print(vals)

In [ ]:
#Relevant coordinate variables are: latitude (code 005001), longitude (code 006001)
#Relevant parameters is: K_Index (code 013044)
lats = np.array([])
lons = np.array([])
K_Indexs = np.array([])

for message in messages:
    LAT_result = DataQuerent(NodePathParser()).query(message, '005001')
    lats=np.concatenate((lats, np.array([LAT_result.results[key][0] for key in LAT_result.results.keys()])))
    LON_result = DataQuerent(NodePathParser()).query(message, '006001')
    lons=np.concatenate((lons,np.array([LON_result.results[key][0] for key in LON_result.results.keys()])))
    K_Index_result = DataQuerent(NodePathParser()).query(message, '013044')
    K_Indexs=np.concatenate((K_Indexs,np.array([K_Index_result.results[key][0] for key in K_Index_result.results.keys()])))   

In [ ]:
# convert numpy array to pandas dataframe
Kindex_dataset = pd.DataFrame({'LAT': lats, 'LON': lons, 'K_index': K_Indexs})
Kindex_dataset

In [ ]:
#Scatter plot of parameter selected
plt.figure(figsize=(6,6))
colvals = preprocessing.minmax_scale(K_Indexs)

plt.scatter(lons, lats, color=cm.rainbow(colvals), marker='.')
plt.xlabel('x')
plt.ylabel('y')
plt.xlim(-70, 70)
plt.ylim(-70, 70)

plt.show()

In [ ]:
#create shape file
#ensure all values are of dtype float (e.g. in case there is a missing value!)
Kindex_dataset['K_index']=Kindex_dataset['K_index'].astype(float)

In [ ]:
# Create geometry column
geometry = [Point(xy) for xy in zip(Kindex_dataset['LON'], Kindex_dataset['LAT'])]

In [ ]:
# Create GeoDataFrame
gdf = gpd.GeoDataFrame(Kindex_dataset, geometry=geometry)

In [ ]:
# Set the coordinate reference system (CRS), WGS84
gdf.set_crs(epsg=4326, inplace=True)

In [ ]:
# Write to shapefile
gdf.to_file(work_dir+'/K_index.shp')

In [ ]:
#check your folder and note the additional messages created
#remove obsolete files, here the seperate messages extracted
for p in glob(work_dir+'/*.bin.*', recursive=True):
    if os.path.isfile(p):
        os.remove(p)

##### Review the new shape file created using ilwis386 or qgis

### GRIB data processing

#### Grib data from the CRM Product
For information on this product see: https://navigator.eumetsat.int/product/EO:EUM:DAT:MSG:CRM?query=crm%20msg&s=advanced

In [ ]:
#dataset
file_in = work_dir+r'/W_XX-EUMETSAT-Darmstadt,SING+LEV+SAT,MET10+CRM_C_EUMG_20240123120000_3.bin'

In [ ]:
CRM = ilwis.RasterCoverage(file_in)
print(CRM.size())

#retrieve the 1.6 micron layer of the dataset
b16 = ilwis.do('selection',CRM,"rasterbands(5)")
print(b16.size())

In [ ]:
#check coordinate system information as well as the map extent - bounding coordinates
coordSys = b16.coordinateSystem()
print(coordSys.toWKT())
print()
print(b16.envelope())

In [ ]:
#retrieve some statistics and the data type
stats = b16.statistics(ilwis.PropertySets.pHISTOGRAM)
min_val = stats[ilwis.PropertySets.pMIN]
max_val = stats[ilwis.PropertySets.pMAX]
print(min_val)
print(max_val)
print()
datadef = b16.datadef()
print(datadef.domain())

In [ ]:
#convert ilwis array to numpy array
#note the poor image visualization due to the fact that values are not properly scaled - stretched
b16_2np = np.fromiter(iter(b16), np.float64, b16.size().linearSize()) 
b16_2np = b16_2np.reshape((b16.size().ysize, b16.size().xsize))

# Plot the 2D array using matplotlib
plt.imshow(b16_2np, vmin=min_val, vmax=max_val, cmap='grey')
plt.title('Selected Layer of Raster Stack')
plt.colorbar(label='Pixel values', shrink=0.6)
plt.axis('off')
plt.show()

In [ ]:
#dislay the color composite, aslo using the green and blue components
#for display using matplotlib
rows = b16.size().ysize
cols = b16.size().xsize
linear_size = cols*rows
print(rows)
print(cols)
print(linear_size)

red = ilwis.do('selection',CRM,"rasterbands(5)")
green = ilwis.do('selection',CRM,"rasterbands(4)")
blue = ilwis.do('selection',CRM,"rasterbands(3)")

redfc = np.fromiter(iter(red), np.ubyte, linear_size) 
redfc = redfc.reshape(rows,cols)
greenfc = np.fromiter(iter(green), np.ubyte, linear_size) 
greenfc = greenfc.reshape(rows,cols)
bluefc = np.fromiter(iter(blue), np.ubyte, linear_size) 
bluefc = bluefc.reshape(rows,cols)

cc = np.dstack((redfc, greenfc, bluefc))

In [ ]:
# Plot the 2D array using matplotlib
plt.imshow(cc)
plt.title('Composite of Raster Stack')
plt.axis('off')
plt.show()

Retrieve the original data once more, use a mask and assign the background to ilwis no data - nan, conduct a linear contract stretch and save the resulting maplist. Check the results also using ilwis386

In [ ]:
#retrieve the 0.6 and 0.8 micron and 1.6 layers of the dataset
crm_cc = ilwis.do('selection',CRM,"rasterbands(3,4,5)")
print(crm_cc.size())

In [ ]:
#import a mask to remove the background
mask = ilwis.RasterCoverage('MSG_0_mask.mpr') # background value of mask = 0

In [ ]:
crm_mod = ilwis.do('mapcalc', 'iff(@1>0,@2,?)', mask, crm_cc)

In [ ]:
#stretch the rasterbands contained in crm_mod
multiple_stretch = []
multiple_bands = ilwis.do('selection',crm_mod,"rasterbands(0..2)") # for specific bands use band number as "rasterbands(0,1,2,6)"
ls = ilwis.do('linearstretch',multiple_bands, 1)
mb_stretch = ilwis.do('setvaluerange', ls, 0, 255, 1)

In [ ]:
#for all pixels with no data set the value to 255 (to create a white background in matplotlib)
rcNew2 = ilwis.do('mapcalc', 'iff(@1==?,255, @1)',mb_stretch) 

In [ ]:
red = ilwis.do('selection',rcNew2,"rasterbands(2)")
green = ilwis.do('selection',rcNew2,"rasterbands(1)")
blue = ilwis.do('selection',rcNew2,"rasterbands(0)")

redfc = np.fromiter(iter(red), np.ubyte, linear_size) 
redfc = redfc.reshape(rows,cols)
redfc_mask = np.ma.masked_where(redfc == 255, redfc)
greenfc = np.fromiter(iter(green), np.ubyte, linear_size) 
greenfc = greenfc.reshape(rows,cols)
greenfc_mask = np.ma.masked_where(greenfc == 255, greenfc)
bluefc = np.fromiter(iter(blue), np.ubyte, linear_size) 
bluefc = bluefc.reshape(rows,cols)
bluefc_mask = np.ma.masked_where(bluefc == 255, bluefc)

cc1 = np.dstack((redfc_mask, greenfc_mask, bluefc_mask))

In [ ]:
# Plot the stretched 3D array using matplotlib
plt.imshow(cc1,extent=[xmin/1000, xmax/1000, ymin/1000, ymax/1000], origin='upper')
plt.xlabel('X Coordinate (km)')
plt.ylabel('Y Coordinate (km)')
plt.title('CRM Map in RGB (1.6, 0.8 and 0.6 Micron) ')
plt.show()

In [ ]:
#store the results - check also using ilwis386
mb_stretch.store('crm_cc.mpl')

#### Convert a map with values to classes - example Cloud Map
See further product information at https://navigator.eumetsat.int/product/EO:EUM:DAT:MSG:CLM?query=clm%20msg&s=advanced

In [ ]:
# CLM input data
file_in = work_dir+'/W_XX-EUMETSAT-Darmstadt,SING+LEV+SAT,MET10+CLM_C_EUMG_20240612111500_3.bin'

In [ ]:
CLM = ilwis.RasterCoverage(file_in)
print(CLM.size())

#retrieve the 1.6 micron layer of the dataset
clm_data = ilwis.do('selection',CLM,"rasterbands(0)")
print(clm_data.size())

In [ ]:
#convert ilwis array to numpy array
clm_data_2np = np.fromiter(iter(clm_data), np.float64, clm_data.size().linearSize()) 
clm_data_2np = clm_data_2np.reshape((clm_data.size().ysize, clm_data.size().xsize))

# Plot the 2D array using matplotlib
plt.imshow(clm_data_2np, vmin=0, vmax=3, cmap='jet')
plt.title('Selected Layer of Raster Stack')
plt.colorbar(label='Pixel values', shrink=0.6)
plt.axis('off')
plt.show()

In [ ]:
#set background to no data
rcNew = ilwis.do('mapcalc', 'iff(@1==3,?,@1)', clm_data)

In [ ]:
# create a new NumericItemRange and fill it with required class items
cltrange = ilwis.NumericItemRange()
cltrange.add(('Water', 0.0, 0.99)) #0
cltrange.add(('Land', 1.0, 1.99)) #1
cltrange.add(('Cloud', 2.0, 2.99)) #2

In [ ]:
#assign the range to a new ItemDomain, slice the map and store the results
#check the reclassified map created using ilwis386 and note the use of the ilwis pre-set "Representation" MPEF_CLMClass.rp# renamed to cloud_class.rp#

#create a new domain from the ranges specified above
clt_dom = ilwis.ItemDomain(cltrange)
        
#perform the raster slicing - assign the values to the domain classes based on the initial value
cloud_cl = ilwis.do('sliceraster', rcNew, clt_dom)

#create a domain with the idential name
cloud_cl.datadef().domain().name('cloud_class') 

#store the map
cloud_cl.store('cloud_class.mpr')

#use ilwis colour representation template available within the sample data set and assign it the name of the output map created
src_file = work_dir+'/MPEF_CLMClass.rp#'
dst_file = work_dir+'/cloud_class.rp#'
shutil.copy(src_file, dst_file)